# Interpolation 

nctoolkit features built in methods for horizontal and vertical interpolation.

### Interpolating to a set of coordinates 

If you want to regrid a dataset to a specified set of coordinates you can `regrid` and a pandas dataframe. The first column of the dataframe should be the longitudes and the second should be latitudes. The example below regrids a sea-surface temperature dataset to a single location with longitude -30 and latitude 50.

In [3]:
import nctoolkit as nc
import pandas as pd
data = nc.open_thredds("https://psl.noaa.gov/thredds/dodsC/Datasets/COBE2/sst.mon.mean.nc")
data.select(timestep = range(0, 12))
coords = pd.DataFrame({"lon":[-30], "lat":[50]})
data.regrid(coords)
data.plot("sst")

:DynamicMap   [variable]
   :Curve   [time]   (value)

## Interpolating to a regular latlon grid

If you want to interpolate to a regular latlon grid, you can use `to_latlon`. `lon` and `lat` specify the minimum and maximum longitudes and latitudes, while `res`, a 2 variable list specifies the resolution. For example, if we wanted to regrid the globe to 0.5 degree north-south by 1 degree east-west resolution, we could do the following:

In [4]:
data = nc.open_thredds("https://psl.noaa.gov/thredds/dodsC/Datasets/COBE2/sst.mon.mean.nc")
data.select(timestep = 0)
data.to_latlon(lon = [-79.5, 79.5], lat = [0.75, 89.75], res = [1, 0.5])
data.plot()

:DynamicMap   []
   :Overlay
      .Image.I     :Image   [lon,lat]   (sst)
      .Coastline.I :Feature   [Longitude,Latitude]

## Interpolating to another dataset's grid

If we are working with two datasets and want to put them on a common grid, we can interpolate one onto the other's grid. We can illustate this with a dataset of global sea surface temperature. Let's start by regridding the first timestep in this dataset to a regular latlon grid covering the North Atlantic.

In [5]:
data1 = nc.open_thredds("https://psl.noaa.gov/thredds/dodsC/Datasets/COBE2/sst.mon.mean.nc")
data1.select(timestep = 0)
data1.to_latlon(lon = [-79.5, 79.5], lat = [-0.75, 89.75], res = [1, 0.5])
data1.plot()

:DynamicMap   []
   :Overlay
      .Image.I     :Image   [lon,lat]   (sst)
      .Coastline.I :Feature   [Longitude,Latitude]

We can then use this new dataset as the target grid in `regrid`. So 

In [6]:
data2 = nc.open_thredds("https://psl.noaa.gov/thredds/dodsC/Datasets/COBE2/sst.mon.mean.nc")
data2.select(timestep = 0)
data2.regrid(data1)
data2.plot()

The first file in dataset used for regridding!


:DynamicMap   []
   :Overlay
      .Image.I     :Image   [lon,lat]   (sst)
      .Coastline.I :Feature   [Longitude,Latitude]

This method will also work using NetCDF files. So, if you wanted you can also use a path to a NetCDF file as the target grid.

## Resampling

If you want to make data more coarse spatially, just use the `resample_grid` method. This will, for example, let you select every 2nd grid grid cell in a north-south and east-west direction. This is illustrated in the example below, where a dataset which has spatial resolution of 1 by 1 degrees is coarsened, so that only every 10th cell is selected in a north-south and east-west. In other words it is now a 10 degrees by 10 degrees dataset.

In [7]:
data = nc.open_thredds("https://psl.noaa.gov/thredds/dodsC/Datasets/COBE2/sst.mon.mean.nc")
data.select(timestep = 0)
data.resample_grid(10)
data.plot()

:DynamicMap   []
   :Overlay
      .Image.I     :Image   [lon,lat]   (sst)
      .Coastline.I :Feature   [Longitude,Latitude]

## Vertical interpolation

We can carry out vertical interpolation using the `vertical_interp` method. This is particularly useful for oceanic data. This is illustrated below by interpolating ocean temperatures from NOAA's World Ocean Atlas for January to a depth of 500 metres. The `vertical_interp` method requires a `levels` argument, which is sea-depth in this case.

In [8]:
data = nc.open_thredds("https://data.nodc.noaa.gov/thredds/dodsC/ncei/woa/temperature/A5B7/1.00/woa18_A5B7_t01_01.nc")
data.select(variables="t_an")
data.vertical_interp(levels= [500])
data.plot()

:DynamicMap   []
   :Overlay
      .Image.I     :Image   [lon,lat]   (t_an)
      .Coastline.I :Feature   [Longitude,Latitude]